In [1]:
# better formatting for large floats
import pandas as pd
pd.options.display.float_format = "{:,.2f}".format

In [2]:
from risk.swaptions import get_swaption_portfolio
import datetime
from utils.db import dbconn
from analytics import init_ontr
import analytics
conn = dbconn('dawndb')
conn.autocommit = True
value_date = datetime.date.today()
init_ontr(value_date)

In [3]:
portf = get_swaption_portfolio(value_date, conn, source_list=["GS"])
portf

Portfolio 2020-01-22

           Product     Index       Notional   Ref Strike Direction      Type      Expiry    Vol  \
ids                                                                                               
SWPTN91   Swaption  IG33 5yr 200,000,000.00 45.13   45.0      Long  receiver  2020-02-19 40.74%   
SWPTN92   Swaption  IG33 5yr 200,000,000.00 45.13   65.0     Short     payer  2020-02-19 75.62%   
SWPTN97   Swaption  IG33 5yr 200,000,000.00 45.13   42.5      Long  receiver  2020-03-18 38.45%   
SWPTN107  Swaption  IG33 5yr 200,000,000.00 45.13   42.5      Long  receiver  2020-03-18 38.45%   
SWPTN108  Swaption  IG33 5yr 200,000,000.00 45.13   55.0     Short     payer  2020-03-18 54.75%   
SWPTN98   Swaption  IG33 5yr 200,000,000.00 45.13   57.5     Short     payer  2020-03-18 57.96%   
SWPTN93   Swaption  IG33 5yr 300,000,000.00 45.13   62.5     Short     payer  2020-03-18 63.80%   
SWPTN103  Swaption  IG33 5yr 200,000,000.00 45.13   42.5      Long  receiver  2020-04-15 39.95%   
SWPTN101  Swaption  IG33 5yr 100,000,000.00 45.13   42.5      Long  receiver  2020-04-15 39.95%   
SWPTN99   Swaption  IG33 5yr 200,000,000.00 45.12   42.5      Long  receiver  2020-04-15 39.96%   
SWPTN102  Swaption  IG33 5yr 100,000,000.00 45.12   57.5     Short     payer  2020-04-15 55.99%   
SWPTN104  Swaption  IG33 5yr 200,000,000.00 45.12   57.5     Short     payer  2020-04-15 55.99%   
SWPTN100  Swaption  IG33 5yr 200,000,000.00 45.12   60.0     Short     payer  2020-04-15 58.42%   
SWPTN105  Swaption  IG33 5yr 200,000,000.00 45.12   42.5      Long  receiver  2020-05-20 41.20%   
SWPTN106  Swaption  IG33 5yr 200,000,000.00 45.12   60.0     Short     payer  2020-05-20 56.55%   

                  PV   Delta   Gamma     Theta      Vega       HY Equiv  
ids                                                                      
SWPTN91   150,061.67 -37.06%  66.00% -3,327.79  4,576.20 -21,825,100.50  
SWPTN92   -20,633.56  -6.40% -13.42%  1,809.79 -1,399.72  -3,765,995.13  
SWPTN97    96,216.26 -21.68%  43.36% -1,761.48  5,166.44 -12,768,492.88  
SWPTN107   96,216.26 -21.68%  43.36% -1,761.48  5,166.44 -12,768,492.88  
SWPTN108 -123,985.48 -26.66% -32.67%  2,590.27 -5,340.77 -15,699,000.27  
SWPTN98  -101,557.29 -21.92% -27.94%  2,453.43 -4,793.54 -12,910,454.18  
SWPTN93  -107,301.85 -15.41% -20.60%  3,231.38 -5,769.27 -13,613,875.38  
SWPTN103  130,102.18 -22.89%  35.40% -1,518.80  6,419.89 -13,477,124.52  
SWPTN101   65,051.09 -22.89%  35.40%   -759.40  3,209.94  -6,738,562.26  
SWPTN99   130,399.30 -22.93%  35.43% -1,520.20  6,424.14 -13,500,437.56  
SWPTN102  -86,043.53 -28.92% -27.46%  1,137.31 -3,432.55  -8,516,333.11  
SWPTN104 -172,087.07 -28.92% -27.46%  2,274.63 -6,865.09 -17,032,666.22  
SWPTN100 -147,765.75 -24.99% -24.50%  2,198.93 -6,373.46 -14,714,847.97  
SWPTN105  161,429.07 -23.06%  29.16% -1,309.02  7,595.96 -13,577,001.50  
SWPTN106 -229,470.13 -31.54% -23.91%  2,020.49 -8,542.41 -18,570,543.35

In [4]:
df = portf._todf()
positions = df.set_index("Index")[["Delta", "Notional"]].prod(axis=1).groupby(level="Index").sum()
positions.name = 'current_delta'
gamma = df.set_index("Index")[["Gamma", "Notional"]].prod(axis=1).groupby(level="Index").sum()
gamma.name = 'gamma'

In [5]:
hedges = pd.read_sql_query("SELECT security_desc, notional FROM list_cds_positions_by_strat(%s) "
                           "WHERE folder in ('IGOPTDEL', 'HYOPTDEL')",
                           conn, params=(value_date,))

In [6]:
def f(s):
    l = s.split(" ")
    return f"{l[1]}{l[3][1:]} {l[4].lower()}r"

hedges["Index"] = hedges["security_desc"].apply(f)
hedges = hedges.rename(columns={"notional": "current hedge"})
hedges = hedges.set_index("Index")["current hedge"]
hedges = hedges.reindex(positions.index, fill_value=0.)
risk = pd.concat([hedges, positions, gamma], axis=1)
risk['net_delta'] = risk["current hedge"] + risk.current_delta
risk

current hedge   current_delta          gamma    net_delta
Index                                                              
IG33 5yr 681,400,000.00 -677,507,134.07 151,731,367.46 3,892,865.93

In [7]:
portf.theta

5758.050875686662